In [66]:
import xarray as xr
import dask as da
import pandas as pd
import numpy as np
import cartopy
import time,os
#import rasterio as rs
import rioxarray
import shapefile
import matplotlib.pyplot as plt
import cartopy.feature as cfeature
from cartopy.feature import ShapelyFeature
import cartopy.io.shapereader as shpreader
from shapely import geometry
import datashader
import hvplot.xarray
import cmocean.cm as cmo
import xcmocean
from scipy import signal, datasets,ndimage
import shutil,netCDF4

In [2]:
from dask.distributed import Client
import dask.array as da
client = Client()
client

2023-02-24 10:00:06,329 - distributed.diskutils - INFO - Found stale lock file and directory '/tmp/dask-worker-space/worker-tymjyv5i', purging
2023-02-24 10:00:06,330 - distributed.diskutils - INFO - Found stale lock file and directory '/tmp/dask-worker-space/worker-rg8f35_7', purging
2023-02-24 10:00:06,330 - distributed.diskutils - INFO - Found stale lock file and directory '/tmp/dask-worker-space/worker-8b3ayah2', purging
2023-02-24 10:00:06,330 - distributed.diskutils - INFO - Found stale lock file and directory '/tmp/dask-worker-space/worker-p4ubdwa_', purging
2023-02-24 10:00:06,330 - distributed.diskutils - INFO - Found stale lock file and directory '/tmp/dask-worker-space/worker-ca5dqz6i', purging
2023-02-24 10:00:06,331 - distributed.diskutils - INFO - Found stale lock file and directory '/tmp/dask-worker-space/worker-i4irt8tl', purging
2023-02-24 10:00:06,331 - distributed.diskutils - INFO - Found stale lock file and directory '/tmp/dask-worker-space/worker-ldpnu7gz', purging

<Client: 'tcp://127.0.0.1:40996' processes=6 threads=36, memory=376.39 GiB>

In [15]:


gfile=r'//home/hunter/roms/NOPP/grids/michael_grd3_CUDEM.nc'
ogfile=r'/home/hunter/roms/NOPP/grids/michael_grd3_CUDEM_SMOOTH.nc'


proj = cartopy.crs.Mercator(central_longitude=-98)
pc = cartopy.crs.PlateCarree()
grd = xr.open_dataset(gfile,chunks={'eta_rho':900,'xi_rho':600}) 
grd=grd.set_coords(('lat_rho','lon_rho'))

grdH=grd.h.load()
grdH = grdH.rename({"lon_rho": "lon", "lat_rho": "lat"})

#glon=np.concatenate((grd1.lon_rho[0,:].values,grd1.lon_rho[:,-1].values,np.flip(grd1.lon_rho[-1,:].values),np.flip(grd1.lon_rho[:,0].values)))  
#glat=np.concatenate((grd1.lat_rho[0,:].values,grd1.lat_rho[:,-1].values,np.flip(grd1.lat_rho[-1,:].values),np.flip(grd1.lat_rho[:,0].values)))  

#llbounds=d = np.column_stack((glon,glat))

In [55]:
H=grdH[:,:].values

grdH_sm=grdH.copy()
###########################################
#np=5
#w = signal.windows.boxcar(np)/np
#H_sm = signal.sepfir2d(H, w, w)
###########################################
sigma=2.0
order=0
mode='reflect'
H_sm=ndimage.gaussian_filter(H, sigma, order=order,mode=mode)
###########################################
\

grdH_sm[:,:]=H_sm

In [56]:
grdH.hvplot.quadmesh(x='lon', y='lat',crs=pc, rasterize=True,clim=(-15,15),cmap='seismic',subplots=True,shared_axes=True)+grdH_sm.hvplot.quadmesh(x='lon', y='lat',crs=pc, rasterize=True,clim=(-15,15),cmap='seismic',subplots=True,shared_axes=True)

:Layout
   .DynamicMap.I  :DynamicMap   []
      :Image   [lon,lat]   (h)
   .DynamicMap.II :DynamicMap   []
      :Image   [lon,lat]   (h)

In [58]:
grdH

<xarray.DataArray 'h' (eta_rho: 650, xi_rho: 550)>
array([[7.97862196, 7.96158743, 7.94818544, ..., 1.49410141, 1.49288785,
        1.50125635],
       [7.9100194 , 7.89606905, 7.88201904, ..., 1.48738241, 1.48724055,
        1.49604881],
       [7.84067726, 7.82953262, 7.81483555, ..., 1.49138713, 1.49155998,
        1.49851644],
       ...,
       [8.74720192, 8.75095463, 8.75604057, ..., 0.5485034 , 0.58726931,
        0.64989537],
       [8.74789333, 8.74393272, 8.74516964, ..., 0.51413804, 0.54333586,
        0.59393656],
       [8.75281906, 8.74671078, 8.74285698, ..., 0.47891384, 0.50462389,
        0.54410696]])
Coordinates:
    lat      (eta_rho, xi_rho) float64 29.75 29.75 29.75 ... 29.78 29.78 29.78
    lon      (eta_rho, xi_rho) float64 -85.41 -85.41 -85.41 ... -85.4 -85.4
Dimensions without coordinates: eta_rho, xi_rho
Attributes:
    long_name:  Final bathymetry at RHO-points
    units:      meter
    field:      bath, scalar

In [59]:
grdH_sm

<xarray.DataArray 'h' (eta_rho: 650, xi_rho: 550)>
array([[7.88190988, 7.87734129, 7.86933742, ..., 1.48978599, 1.4938482 ,
        1.49563889],
       [7.85577961, 7.8513266 , 7.8435678 , ..., 1.49239018, 1.49616673,
        1.49783719],
       [7.80942092, 7.80517006, 7.79783425, ..., 1.4976729 , 1.50102515,
        1.50251616],
       ...,
       [8.7542295 , 8.75446197, 8.75469261, ..., 0.56958124, 0.58602611,
        0.59646812],
       [8.75133083, 8.75145774, 8.75158348, ..., 0.54597137, 0.56174598,
        0.57165563],
       [8.74987177, 8.74990211, 8.74991555, ..., 0.53231641, 0.5475898 ,
        0.55713472]])
Coordinates:
    lat      (eta_rho, xi_rho) float64 29.75 29.75 29.75 ... 29.78 29.78 29.78
    lon      (eta_rho, xi_rho) float64 -85.41 -85.41 -85.41 ... -85.4 -85.4
Dimensions without coordinates: eta_rho, xi_rho
Attributes:
    long_name:  Final bathymetry at RHO-points
    units:      meter
    field:      bath, scalar

In [80]:
#Create new grid file
shutil.copy(gfile,ogfile)
#wrtiting data put. 
nc = netCDF4.Dataset(ogfile, "r+", format="NETCDF4")
h=nc['h']
hraw=nc['hraw']
hraw[:,:]=h[:,:]
h[:,:]=grdH_sm.values

nc.close()


In [81]:
grd = xr.open_dataset(ogfile,chunks={'eta_rho':900,'xi_rho':600}) 
grd=grd.set_coords(('lat_rho','lon_rho'))
grdH=grd.h.load()
grdH = grdH.rename({"lon_rho": "lon", "lat_rho": "lat"})

grdHraw=grd.hraw.load()
grdHraw = grdHraw.rename({"lon_rho": "lon", "lat_rho": "lat"})
grdHraw =np.squeeze(grdHraw)

In [82]:
grdH.hvplot.quadmesh(x='lon', y='lat',crs=pc, rasterize=True,clim=(-15,15),cmap='seismic',subplots=True,shared_axes=True)+grdHraw.hvplot.quadmesh(x='lon', y='lat',crs=pc, rasterize=True,clim=(-15,15),cmap='seismic',subplots=True,shared_axes=True)

:Layout
   .DynamicMap.I  :DynamicMap   []
      :Image   [lon,lat]   (h)
   .DynamicMap.II :DynamicMap   []
      :Image   [lon,lat]   (hraw)

In [71]:
grdHraw


<xarray.DataArray 'hraw' (bath: 1, eta_rho: 650, xi_rho: 550)>
array([[[7.97862196, 7.96158743, 7.94818544, ..., 1.49410141,
         1.49288785, 1.50125635],
        [7.9100194 , 7.89606905, 7.88201904, ..., 1.48738241,
         1.48724055, 1.49604881],
        [7.84067726, 7.82953262, 7.81483555, ..., 1.49138713,
         1.49155998, 1.49851644],
        ...,
        [8.74720192, 8.75095463, 8.75604057, ..., 0.5485034 ,
         0.58726931, 0.64989537],
        [8.74789333, 8.74393272, 8.74516964, ..., 0.51413804,
         0.54333586, 0.59393656],
        [8.75281906, 8.74671078, 8.74285698, ..., 0.47891384,
         0.50462389, 0.54410696]]])
Coordinates:
    lat      (eta_rho, xi_rho) float64 29.75 29.75 29.75 ... 29.78 29.78 29.78
    lon      (eta_rho, xi_rho) float64 -85.41 -85.41 -85.41 ... -85.4 -85.4
Dimensions without coordinates: bath, eta_rho, xi_rho
Attributes:
    long_name:  Working bathymetry at RHO-points
    units:      meter
    field:      bath, scalar